In [1]:

"""
This program aims at transforming a 3D point cloud by matching it onto a set
of geographical coordinates, in order to display it in geographical information systems.
IN : - 3D model in .uv3 format, whose indicated path will be used to get the point selections for the least square fitting
	- chosen EPSG 
OUT : georeferenced 3D model in ply or uv3 format (depending on the format of the input file), in the chosen EPSG 
"""

import numpy as np
import json
import sys
import struct
import click

sys.path.append('../share')
from least_squares_matching import least_squares_matching

In [2]:
@click.command()
@click.option('--file', help='path to ply (ascii) or uv3 (binary) format')
@click.option('--source', help='List of selected points on the source point cloud')
@click.option('--target', help='List of selected points on the target point cloud')
@click.option('--epsg', default=None, help='SRID of the spatial coordinate system of the target point cloud')

file_format = file.split('.')[-1]

Usage: ipykernel_launcher.py [OPTIONS]
Try "ipykernel_launcher.py --help" for help.

Error: no such option: -f


SystemExit: 2

/home/descombe/anaconda3/lib/python3.7/site-packages/IPython/core/interactiveshell.py:3334: UserWarning: To exit: use 'exit', 'quit', or Ctrl-D.
  warn("To exit: use 'exit', 'quit', or Ctrl-D.", stacklevel=1)


In [ ]:
F,R,t = least_squares_matching(source,target)

if epsg is not None: # the transformation is a geolocalisation
    file_out = file.replace('.', '-epsg%s.' % epsg)
else: # the transformation is a point cloud matching
    file_out = file.replace('.', '-matched.')
    
if file_format == 'ply': # ply ascii format
    f_in = open(file, 'r').readlines()
    pt_idx = f_in.index('end_header\n')
    points = f_in[pt_idx+1:]

    with open(file_out, 'w') as f_out:
        for line in f_in[:pt_idx+1]:
            f_out.write("%s" %(line.replace('float', 'double')))
        for pt in points:
            colors = ' '.join(x for x in pt.split()[3:])
            camera_pose = [np.float(xx) for xx in pt.split()[:3]]
            coors = np.array(np.matmul(np.transpose(R), np.subtract(F * np.array(camera_pose), t)), dtype=np.float64)
            f_out.write(str(coors[0]) + " " + str(coors[1]) + " " + str(coors[2]) + " " + colors + "\n")

elif file_format == 'uv3': # uv3 binary format
    with open(file, 'rb') as f_in:
        with open(file_out, 'wb') as f_out:
            while True:
                byte = f_in.read(28)
                
                if not byte:
                    break
                    
                x,y,z,a,r,g,b = struct.unpack('<dddBBBB', byte)
                xx,yy,zz = np.matmul(np.transpose(R), np.subtract(F * np.array([x,y,z]), t))
                export = struct.pack('<dddBBBB', xx, yy, zz, a, r, g, b)
                f_out.write(export)

else:
    print('unknown format')


2311014.77510986 5035503.949185701 11.011126326369833
2311015.459629892 5035508.367367239 8.773623860847513
2311014.4044739096 5035502.450353117 7.769882280713592
2311014.1962706367 5035501.011937568 10.1626282213103
2311014.295703857 5035501.770254373 7.663930630400403
2311014.475729255 5035502.807695932 7.03682432493475
2311013.439575411 5035496.183671844 6.72365613235672
2310979.8424778106 5035505.046543007 5.717567695550747
2311014.5958932727 5035503.818521903 14.530266744507458
2311013.276571916 5035496.196683736 8.761320930945926
2311002.9479951966 5035506.37547981 15.391562875092912
2310977.1640032814 5035522.132040589 11.448901230323967
2310978.202603553 5035521.823410509 6.8510662609965225
2311013.893679393 5035500.307669353 13.012493828226217
2310982.547239354 5035508.754330485 2.090547680218423
2310987.5886178142 5035499.033551588 3.028849433984983
2310985.70773805 5035496.470917846 2.369312745835847
2311014.939509107 5035505.353944806 8.257300662285665
2311015.4391713417 50

2311015.676186345 5035508.347795759 8.493435627962047
2311013.819564237 5035498.998337257 4.252174288151446
2311014.415330836 5035502.470526821 7.55585243710624
2311014.2201466225 5035501.431152782 6.1842489617777945
2311009.4762960067 5035505.421815005 10.713816185632131
2311014.4963198 5035502.909889946 6.8710497789765945
2310979.9226770084 5035507.259884238 8.854032416422942
2311013.889437408 5035499.502358759 5.9731179475927405
2310980.4335742663 5035510.587249582 4.975439367895407
2311013.778870547 5035498.874072664 5.908777625839122
2311014.332113176 5035501.851282997 10.055211024445079
2311014.979860562 5035506.414987123 9.788010100425538
2311013.7372891475 5035498.630722097 5.885721327728596
2310980.5449340055 5035510.935586043 4.987894781938442
2311013.7844520295 5035499.626555153 3.413496297209453
2311013.7152604638 5035498.541027531 9.149894297676045
2310979.732697134 5035505.240855877 5.5630700557318296
2310988.743061662 5035502.7268249225 3.0814340282663624
2310979.1304180

2311013.8247666727 5035499.16403117 8.018847127260123
2310980.565263733 5035509.130048154 9.041390878338367
2311015.4332717503 5035508.2146485215 5.2385604982862475
2310992.9501693086 5035502.7227378655 11.580377722481535
2310980.649189455 5035511.295666141 8.975448988123858
2310985.7136976435 5035496.347612772 2.2214288480223785
2310980.543356295 5035510.674380608 9.360017648029599
2311014.828103854 5035505.935083042 5.128725046107924
2311013.314986914 5035496.216730686 6.2535978295635095
2311014.31078329 5035501.735362722 9.89455353896242
2311014.9528344735 5035506.440593925 4.165744209293515
2311014.699379982 5035503.9862373425 9.014796669482553
2311013.676133325 5035498.290416701 4.057888721331747
2311013.8330269647 5035499.2946140105 8.037133180685185
2310979.301104645 5035503.661474409 5.277263971956077
2311014.2093631355 5035501.345629976 13.010740539851115
2311013.3702728148 5035496.69350504 8.541823352960568
2310997.168775856 5035501.446156725 10.030197185606724
2310981.859014

2310979.7708098013 5035506.709938229 8.327055850932298
2310979.98955825 5035507.569587326 3.513134996968994
2311014.7561348984 5035504.200305752 9.85283382314903
2310979.152296131 5035502.349036034 5.881205317278759
2311014.212687351 5035501.204841899 3.5026995613209326
2310979.842788452 5035506.684571859 12.258118908287582
2311015.334781488 5035507.598538945 8.906698091877614
2311015.7169467784 5035509.694975227 4.835110750959548
2310979.781422841 5035504.553325034 6.074051097396683
2310980.5583774885 5035509.200855351 13.282165661815466
2310979.872165947 5035504.865258989 6.104496642968972
2310979.282582205 5035503.73261286 8.42738674840129
2310989.669488668 5035497.589482511 2.8551913795101784
2311014.7209248147 5035504.284502428 8.313149309876184
2311013.92156058 5035499.582339344 3.8222572887330326
2311014.909728356 5035506.206179803 4.724563700842184
2311016.6972383377 5035511.452904746 10.246798319595301
2310979.637260283 5035505.734952798 4.213990890793606
2311014.346288124 503

2311013.5981797636 5035497.842481147 5.425991810693747
2311013.887987741 5035499.721759585 6.307368361659586
2311013.6060576336 5035497.63759338 5.407454562900268
2311013.6258626184 5035498.012326596 6.100716883627937
2311013.5030901586 5035497.26028539 4.655290125364787
2311013.5291806357 5035497.4487056015 6.035936803175443
2310979.8775243885 5035507.761857482 6.940664898808578
2311015.3944773735 5035507.864179814 9.256328465852414
2310979.1730673076 5035502.607122047 4.175992117693303
2311013.76376708 5035498.805850388 8.913343435844363
2310980.4577301648 5035508.589386212 8.047674241185304
2311015.6526222415 5035509.469384982 7.470258741421072
2310979.8008773914 5035506.765378473 5.356596186691777
2311014.2918445757 5035501.842612408 6.374000331879322
2310988.739163596 5035498.100805243 2.6303003896581467
2311013.7179696737 5035498.548465669 6.164486615223359
2310980.188604537 5035508.190301431 15.940298735284046
2311015.615945178 5035509.6866727155 9.579702145158713
2310980.391466

...

2311031.8698502793 5035496.128577722 18.72873004022032
2311031.7443441423 5035493.009757217 16.912077511368825
2311023.2726134043 5035497.869525215 13.382819255819859
2311031.4049764923 5035493.979770036 13.248470310592154
2311031.320857897 5035493.095874902 16.75985959847185
2311009.813786533 5035505.259100358 15.59932604120033
2311022.811306977 5035497.976117643 13.334953632182678
2311030.2285167673 5035489.441144541 11.230705087691504
2311031.9698761255 5035494.635984074 17.41188518674152
2311011.5904560145 5035512.983091933 8.970690103009767
2311028.0701679657 5035493.61052002 3.570159103962032
2311030.1959951785 5035489.639002589 11.266493391055578
2311032.05457708 5035494.6114667365 17.34073384205367
2311031.889817562 5035494.6422408065 17.25840282634695
2311019.6138622626 5035498.832573621 12.421868956005177
2311019.0674400297 5035495.156364552 4.055091366940472
2311031.9298694422 5035496.288462407 17.981783090874593
2311022.454455029 5035494.454086437 9.204583464095025
2311003.

2311013.0843839445 5035512.799046084 7.868328378327801
2311027.596803844 5035493.667961297 4.28813208276992
2311015.1915652296 5035495.842904294 8.93758660855495
2311032.6195238573 5035492.827567422 18.94750889919302
2311009.975216464 5035505.343868775 3.4190456149454023
2311030.966655276 5035493.2093112795 6.5403773352247025
2311006.7399717057 5035505.78711405 13.300928283557566
2311029.5051144874 5035493.383761774 4.313038386565958
2310999.894127306 5035507.728589218 5.5165318246623585
2311031.1084788707 5035494.373162515 19.34227767238478
2311005.0324842613 5035506.222979819 5.747365390359319
2311022.3444581837 5035496.33256709 10.01698993625476
2311000.9727042345 5035506.971648206 12.881297191805938
2311000.706735266 5035507.122177199 7.641524574063829
2311019.8085701093 5035494.461067544 3.1751735244339145
2311001.207658181 5035506.714237755 10.024612227164468
2310999.8448990337 5035507.283955762 9.450381152657647
2311013.5016752086 5035496.16406607 8.791216922011104
2311029.70870

2311028.9264835706 5035488.0184460925 5.91428823907253
2311019.3102007313 5035495.109171813 3.859658178694108
2310999.2093377993 5035503.466514905 7.376061302438172
2311007.569129728 5035505.734715956 8.550859998265864
2311030.645209962 5035491.434814039 13.255281087284558
2311005.6978199044 5035505.976006971 15.974208242067855
2311019.1666144785 5035495.178184828 7.867525613068095
2311029.1544286553 5035493.473224798 6.6640645058861265
2311009.857974307 5035505.3175073555 11.836857793651472
2311032.09337563 5035496.255162031 17.078132834296518
2311004.303593261 5035505.236014622 11.366654808828354
2311005.544878496 5035506.13361223 16.000834925113182
2311031.935574587 5035496.3241252005 17.064660342975134
2311027.0341429524 5035493.835632543 8.489328866631901
2311032.064892477 5035492.980569744 15.566562089341796
2311031.10709016 5035493.169295297 11.526997511122206
2311012.2033125497 5035512.875280904 8.824997490795086
2311021.668009283 5035494.863998588 4.575875082503869
2311029.387

2311025.0446633 5035494.143008711 6.740837483044582
2311010.0915490654 5035506.383583904 6.871536285007567
2311005.4804859324 5035506.119976487 6.40837158140762
2311030.7757006297 5035491.700231739 4.321635112747215
2311025.8810383063 5035493.994287725 6.870206604552008
2311021.210751226 5035494.834224192 6.514287662837411
2311029.295284713 5035493.46019781 7.065795881054811
2311031.0614162227 5035492.451346118 4.2880740796816275
2311007.786730592 5035505.701943861 6.60629926493234
2311002.5425607665 5035506.66215398 2.9798920817848122
2311022.9551161365 5035494.49511671 6.5723382304568965
2311028.5523231355 5035493.534439663 6.869093798287512
2311014.437264639 5035495.961470156 6.079699817597697
2311026.1974504874 5035493.9396035755 6.733502449011611
2311013.555425076 5035512.539628984 7.410128100877925
2311014.1245409064 5035496.055440468 6.058552971642946
2311029.6628722562 5035488.240317477 4.388269349597324
2311010.086806602 5035506.319411369 6.632143849586823
2311030.8512767046 5

2311028.7033254607 5035493.566421985 7.974281519462125
2311030.9788754755 5035493.176497852 9.397435121977049
2311005.1573255453 5035505.61701551 9.059501291627702
2311001.1403060853 5035507.132075261 6.910557471034621
2311029.364949789 5035493.648859182 9.59196630821296
2311034.483381489 5035492.257936164 19.19608362815301
2311021.1520892093 5035494.78019631 5.796150776863186
2311022.860314717 5035494.685743291 7.305822712280777
2311024.530534383 5035494.212732842 5.850589655992018
2311034.895425238 5035492.20562574 19.237597412054985
2311034.527969777 5035492.265934799 19.172115019979753
2311012.833273742 5035486.962470987 3.3982503787650886
2311009.9982112506 5035505.581038365 6.1334272881072
2311034.6542457356 5035491.967302288 18.96139144992297
2311023.4340471243 5035494.43794717 8.801235580657885
2311005.2928531696 5035505.207820736 10.138066448751761
2311012.9138141605 5035486.914979934 3.3904289907796494
2311011.0865455796 5035512.99931444 7.452785865289628
2311024.4957538485 5